# 02.6 Overall Health by State - Geospatial Analysis

1. Imports and display options
1. Data prep
1. Geospatial analysis

## 1. Imports and display options

In [19]:
import pandas as pd
import os
import matplotlib
import folium
import json
import geopandas as gpd

In [3]:
#Creating a path to the root directory for this project

path = r'C:\Users\theva\Documents\Data Analyses\BRFSS'

In [40]:
#Importing data

df = pd.read_pickle(os.path.join(path, '02 Data','Prepared Data', 'BRFSS Overall Health by State TABLEAU.pkl'))
us_geo = gpd.read_file(os.path.join(path, '02 Data','Original Data', 'us-states.json'))

In [41]:
#Checking df

df.shape

(385, 35)

In [42]:
#Checking df

df.head()

location  year  BMI: Obese (BMI 30.0 - 99.8)  \
0  Alabama  2015                          35.6   
1  Alabama  2016                          35.7   
2  Alabama  2017                          36.3   
3  Alabama  2018                          36.2   
4  Alabama  2019                          36.1   

   BMI: Overweight (BMI 25.0-29.9)  BMI: Normal Weight (BMI 18.5-24.9)  \
0                             33.0                                28.9   
1                             33.8                                28.4   
2                             33.9                                28.5   
3                             33.4                                28.4   
4                             34.2                                27.5   

   BMI: Underweight (BMI 12.0-18.4)  General health: Excellent  \
0                               2.4                       16.2   
1                               2.1                       15.2   
2                               1.3                       15.4   
3                               2.0                       14.5   
4                               2.2                       15.4   

   General health: Very good  General health: Good  General health: Fair  ...  \
0                       29.1                  32.5                  15.2  ...   
1                       29.8                  32.5                  15.7  ...   
2                       28.2                  33.1                  16.2  ...   
3                       28.6                  34.0                  15.7  ...   
4                       29.5                  32.4                  16.2  ...   

   Vegetables eaten: Daily  Vegetables eaten: Not daily  \
0                     72.2                         27.8   
1                      NaN                          NaN   
2                     80.7                         19.3   
3                      NaN                          NaN   
4                     77.7                         22.3   

   Aerobic activity per week: Over 150 min  \
0                                     44.6   
1                                      NaN   
2                                     42.8   
3                                      NaN   
4                                     44.8   

   Aerobic activity per week: Under 150 min  \
0                                      55.4   
1                                       NaN   
2                                      57.2   
3                                       NaN   
4                                      55.2   

   Met physical activity guidelines: Yes  \
0                                   16.7   
1                                    NaN   
2                                   16.1   
3                                    NaN   
4                                   17.6   

   Met physical activity guidelines: No  Strength training: 2x+ per week  \
0                                  83.3                             25.8   
1                                   NaN                              NaN   
2                                  83.9                             26.0   
3                                   NaN                              NaN   
4                                  82.4                             29.2   

   Strength training: 1x- per week  Physically active in last month: Yes  \
0                             74.2                                  68.1   
1                              NaN                                  70.6   
2                             74.0                                  68.0   
3                              NaN                                  69.3   
4                             70.8                                  68.5   

   Physically active in last month: No  
0                                 31.9  
1                                 29.4  
2                                 32.0  
3                                 30.7  
4                                 31.5  

[5 rows x 35 columns]

In [43]:
#Checking us_geo

us_geo.head()

id        name  \
0  AL     Alabama   
1  AK      Alaska   
2  AZ     Arizona   
3  AR    Arkansas   
4  CA  California   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [44]:
#Adjusting display settings

pd.set_option('display.max_rows', 200)
pd.set_option('display.max_colwidth', None)

%matplotlib inline

# 2. Data prep

In [45]:
# Dropping non-necessary column from us_geo

us_geo.drop(columns = 'id', inplace = True)
us_geo.head()

name  \
0     Alabama   
1      Alaska   
2     Arizona   
3    Arkansas   
4  California   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [46]:
# Dropping national averages as they will prevent a geospatial analysis

df = df.loc[(df['location'] != 'All States and DC (median) **') &
            (df['location'] != 'All States, DC and Territories (median) **')]

In [47]:
# Getting column names

df.columns

Index(['location', 'year', 'BMI: Obese (BMI 30.0 - 99.8)',
       'BMI: Overweight (BMI 25.0-29.9)', 'BMI: Normal Weight (BMI 18.5-24.9)',
       'BMI: Underweight (BMI 12.0-18.4)', 'General health: Excellent',
       'General health: Very good', 'General health: Good',
       'General health: Fair', 'General health: Poor',
       'Health status: Good or Better', 'Health status: Fair or Poor',
       'Doc visit: Past year', 'Doc visit: Past 2 years',
       'Doc visit: Past 5 years', 'Doc visit: 5+ years ago',
       'Doc visit: Never', 'Concentrate, remember, decide: Difficult',
       'Concentrate, remember, decide: Not difficult',
       'Bad mental health days: 0', 'Bad mental health days: 1-13',
       'Bad mental health days: 14+', 'Fruit eaten: Daily',
       'Fruit eaten: Not daily', 'Vegetables eaten: Daily',
       'Vegetables eaten: Not daily',
       'Aerobic activity per week: Over 150 min',
       'Aerobic activity per week: Under 150 min',
       'Met physical activity g

In [48]:
# Dropping calculated health statuses and negative response to binary question pairs, 
# i.e.: keeping 'Fruit eaten: Daily' and dropping 'Fruit eaten: Not daily'.

df.drop(columns=['year',
                 'Health status: Good or Better',
                 'Health status: Fair or Poor',
                 'Concentrate, remember, decide: Not difficult',
                 'Fruit eaten: Not daily',
                 'Vegetables eaten: Not daily',
                 'Aerobic activity per week: Under 150 min',
                 'Met physical activity guidelines: No',
                 'Strength training: 1x- per week',
                 'Physically active in last month: No'], inplace=True)

In [49]:
#Checking changes

df.head()

location  BMI: Obese (BMI 30.0 - 99.8)  BMI: Overweight (BMI 25.0-29.9)  \
0  Alabama                          35.6                             33.0   
1  Alabama                          35.7                             33.8   
2  Alabama                          36.3                             33.9   
3  Alabama                          36.2                             33.4   
4  Alabama                          36.1                             34.2   

   BMI: Normal Weight (BMI 18.5-24.9)  BMI: Underweight (BMI 12.0-18.4)  \
0                                28.9                               2.4   
1                                28.4                               2.1   
2                                28.5                               1.3   
3                                28.4                               2.0   
4                                27.5                               2.2   

   General health: Excellent  General health: Very good  General health: Good  \
0                       16.2                       29.1                  32.5   
1                       15.2                       29.8                  32.5   
2                       15.4                       28.2                  33.1   
3                       14.5                       28.6                  34.0   
4                       15.4                       29.5                  32.4   

   General health: Fair  General health: Poor  ...  \
0                  15.2                   7.0  ...   
1                  15.7                   6.9  ...   
2                  16.2                   7.1  ...   
3                  15.7                   7.2  ...   
4                  16.2                   6.5  ...   

   Concentrate, remember, decide: Difficult  Bad mental health days: 0  \
0                                      15.0                        NaN   
1                                      14.3                        NaN   
2                                      15.8                        NaN   
3                                      15.8                        NaN   
4                                      16.7                       58.0   

   Bad mental health days: 1-13  Bad mental health days: 14+  \
0                           NaN                          NaN   
1                           NaN                          NaN   
2                           NaN                          NaN   
3                           NaN                          NaN   
4                          24.5                         17.5   

   Fruit eaten: Daily  Vegetables eaten: Daily  \
0                51.7                     72.2   
1                 NaN                      NaN   
2                55.2                     80.7   
3                 NaN                      NaN   
4                53.9                     77.7   

   Aerobic activity per week: Over 150 min  \
0                                     44.6   
1                                      NaN   
2                                     42.8   
3                                      NaN   
4                                     44.8   

   Met physical activity guidelines: Yes  Strength training: 2x+ per week  \
0                                   16.7                             25.8   
1                                    NaN                              NaN   
2                                   16.1                             26.0   
3                                    NaN                              NaN   
4                                   17.6                             29.2   

   Physically active in last month: Yes  
0                                  68.1  
1                                  70.6  
2                                  68.0  
3                                  69.3  
4                                  68.5  

[5 rows x 25 columns]

In [56]:
# Making a dataframe of mean values per state

df_to_plot = df.groupby('location').mean().reset_index().round(1)
df_to_plot

location  BMI: Obese (BMI 30.0 - 99.8)  \
0                Alabama                          37.0   
1                 Alaska                          31.5   
2                Arizona                          30.0   
3               Arkansas                          36.4   
4             California                          26.3   
5               Colorado                          23.0   
6            Connecticut                          27.8   
7               Delaware                          32.9   
8   District of Columbia                          23.6   
9                Florida                          28.1   
10               Georgia                          32.5   
11                  Guam                          32.2   
12                Hawaii                          24.2   
13                 Idaho                          29.4   
14              Illinois                          31.9   
15               Indiana                          34.3   
16                  Iowa                          34.7   
17                Kansas                          34.1   
18              Kentucky                          36.1   
19             Louisiana                          36.8   
20                 Maine                          30.6   
21              Maryland                          31.2   
22         Massachusetts                          25.2   
23              Michigan                          33.5   
24             Minnesota                          29.4   
25           Mississippi                          38.5   
26              Missouri                          33.9   
27               Montana                          27.1   
28              Nebraska                          33.5   
29                Nevada                          28.5   
30         New Hampshire                          29.0   
31            New Jersey                          27.0   
32            New Mexico                          30.7   
33              New York                          26.6   
34        North Carolina                          32.9   
35          North Dakota                          33.5   
36                  Ohio                          33.9   
37              Oklahoma                          35.8   
38                Oregon                          29.3   
39          Pennsylvania                          31.5   
40           Puerto Rico                          32.3   
41          Rhode Island                          28.6   
42        South Carolina                          34.3   
43          South Dakota                          32.4   
44             Tennessee                          34.7   
45                 Texas                          34.2   
46                  Utah                          27.4   
47               Vermont                          27.0   
48        Virgin Islands                          34.0   
49              Virginia                          31.0   
50            Washington                          28.1   
51         West Virginia                          38.6   
52             Wisconsin                          32.3   
53               Wyoming                          29.6   

    BMI: Overweight (BMI 25.0-29.9)  BMI: Normal Weight (BMI 18.5-24.9)  \
0                              33.4                                27.6   
1                              35.0                                32.0   
2                              35.4                                32.4   
3                              33.1                                28.5   
4                              35.9                                35.6   
5                              35.7                                39.1   
6                              36.1                                34.2   
7                              35.3                                30.0   
8                              31.6                                42.8   
9                              36.2                                33.6   


In [93]:
# merging dataframes

geo_df = pd.merge(us_geo, df_to_plot, how='left', left_on='name', right_on='location', indicator=True)

In [58]:
#checking merge

geo_df['_merge'].value_counts()

both          50
left_only      0
right_only     0
Name: _merge, dtype: int64

In [59]:
#checking merge

geo_df.head()

name  \
0     Alabama   
1      Alaska   
2     Arizona   
3    Arkansas   
4  California   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [94]:
# Dropping unnedded columns

geo_df.drop(columns = ['name', '_merge'], inplace=True)
geo_df.head()

geometry  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

# 3. Geospatial analysis

### 3.1 Defining the mapping function

In [62]:
# Getting map center point
x_center = geo_df.centroid.x.mean()
y_center = geo_df.centroid.y.mean()
print(x_center, y_center)

-93.8092064016807 39.62510389893046


C:\Users\theva\AppData\Local\Temp\ipykernel_10604\3947829767.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  x_center = geo_df.centroid.x.mean()
C:\Users\theva\AppData\Local\Temp\ipykernel_10604\3947829767.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  y_center = geo_df.centroid.y.mean()


In [172]:
#Plots a map based on the variable sent to the function

def plot_map(var):
    # Setup a folium map at a high-level zoom
    this_map = folium.Map(location = [y_center, x_center], zoom_start = 2)

    # Making choropleth
    folium.Choropleth(
        geo_data = geo_df, 
        data = geo_df,
        columns = ['location', var],
        key_on = 'feature.properties.location',
        fill_color = 'Blues',
        nan_fill_color = 'Black',
        fill_opacity=1,
        line_opacity=0.3,
        legend_name = str('Percent '+var),
#        bins = 4
    ).add_to(this_map)


    #Map style
    folium.TileLayer('cartodbpositron').add_to(this_map)

    #tooltip base shading
    style_function = lambda x: {'fillColor': '#ffffff', 
                                'color':'#000000', 
                                'fillOpacity': 0, 
                                'weight': 0}
    #tooltip hover-over shading
    highlight_function = lambda x: {'fillColor': '#000000', 
                                    'color':'#000000', 
                                    'fillOpacity': 0.3, 
                                    'weight': 0.1}

    #State names
    state_name = folium.features.GeoJson(
        geo_df,
        control=False,
        style_function = style_function,
        highlight_function = highlight_function,
        tooltip=folium.features.GeoJsonTooltip(
            fields=['location', var],
            aliases=['State: ', 'Percent:'],
            style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 1px;") 
        )
    )
    this_map.add_child(state_name)
    this_map.keep_in_front(state_name)

    #Map title
    map_title = str('Percent per State: '+var)
    title_html ='''
                <h3 align="center" style="font-size:16px"><b>{}</b></h3>
                '''.format(map_title) 
    this_map.get_root().html.add_child(folium.Element(title_html))

    display(this_map) # Showing map
    
    # Printing top 5 of this variable
    temp = geo_df[['location', var]].sort_values(var, ascending=False)
    print('\nTop 5 \"'+var+'\" states:')
    for i in range(0,5):
        print(str(i+1) + '. ' + str(temp.iloc[i]['location']) + '\t\t' + str(temp.iloc[i][var]) + '%')

    # Printing bottom 5 of this variable
    temp = geo_df[['location', var]].sort_values(var, ascending=True)
    print('\nBottom 5 \"'+var+'\" states:')
    for i in range(0,5):
        print(str(i+1) + '. ' + str(temp.iloc[i]['location']) + '\t\t' + str(temp.iloc[i][var]) + '%')

### 3.2 BMI maps

In [173]:
map_list = ['BMI: Obese (BMI 30.0 - 99.8)',
              'BMI: Overweight (BMI 25.0-29.9)',
              'BMI: Normal Weight (BMI 18.5-24.9)',
              'BMI: Underweight (BMI 12.0-18.4)']

for m in map_list:
    plot_map(m)


Top 5 "BMI: Obese (BMI 30.0 - 99.8)" states:
1. West Virginia		38.6%
2. Mississippi		38.5%
3. Alabama		37.0%
4. Louisiana		36.8%
5. Arkansas		36.4%

Bottom 5 "BMI: Obese (BMI 30.0 - 99.8)" states:
1. Colorado		23.0%
2. Hawaii		24.2%
3. Massachusetts		25.2%
4. California		26.3%
5. New York		26.6%



Top 5 "BMI: Overweight (BMI 25.0-29.9)" states:
1. Nevada		37.2%
2. New Jersey		36.8%
3. Montana		36.5%
4. Florida		36.2%
5. New Hampshire		36.2%

Bottom 5 "BMI: Overweight (BMI 25.0-29.9)" states:
1. Arkansas		33.1%
2. West Virginia		33.2%
3. Louisiana		33.3%
4. Alabama		33.4%
5. Mississippi		33.4%



Top 5 "BMI: Normal Weight (BMI 18.5-24.9)" states:
1. Colorado		39.1%
2. Hawaii		38.8%
3. Massachusetts		37.4%
4. Vermont		37.1%
5. Utah		36.0%

Bottom 5 "BMI: Normal Weight (BMI 18.5-24.9)" states:
1. Mississippi		26.3%
2. West Virginia		26.4%
3. Alabama		27.6%
4. Oklahoma		28.1%
5. Louisiana		28.1%



Top 5 "BMI: Underweight (BMI 12.0-18.4)" states:
1. Hawaii		2.7%
2. Arizona		2.2%
3. California		2.2%
4. Colorado		2.2%
5. New York		2.2%

Bottom 5 "BMI: Underweight (BMI 12.0-18.4)" states:
1. South Dakota		1.3%
2. Alaska		1.4%
3. North Dakota		1.4%
4. Iowa		1.4%
5. Wyoming		1.6%


<div class='alert alert-block alert-info'>
   ...<br>...<br>...<br>
   </div>

### 3.2 Doctor visits

In [174]:
map_list = ['Doc visit: Past year',
            'Doc visit: Past 2 years',
            'Doc visit: Past 5 years',
            'Doc visit: 5+ years ago',
            'Doc visit: Never']

for m in map_list:
    plot_map(m)


Top 5 "Doc visit: Past year" states:
1. Rhode Island		82.4%
2. West Virginia		79.6%
3. Massachusetts		78.6%
4. Delaware		78.4%
5. New Jersey		77.8%

Bottom 5 "Doc visit: Past year" states:
1. Alaska		62.9%
2. Utah		65.4%
3. Colorado		65.8%
4. Idaho		65.9%
5. Wyoming		66.0%



Top 5 "Doc visit: Past 2 years" states:
1. California		16.8%
2. New Mexico		15.6%
3. Colorado		15.6%
4. Washington		15.6%
5. Oregon		15.0%

Bottom 5 "Doc visit: Past 2 years" states:
1. West Virginia		8.5%
2. Rhode Island		9.9%
3. North Carolina		10.0%
4. Florida		10.2%
5. Louisiana		10.4%



Top 5 "Doc visit: Past 5 years" states:
1. Alaska		10.3%
2. Colorado		9.8%
3. Utah		9.8%
4. Idaho		9.3%
5. North Dakota		9.1%

Bottom 5 "Doc visit: Past 5 years" states:
1. Rhode Island		4.3%
2. West Virginia		5.0%
3. Massachusetts		5.1%
4. Delaware		5.3%
5. New Jersey		5.4%



Top 5 "Doc visit: 5+ years ago" states:
1. Wyoming		11.1%
2. Alaska		10.9%
3. Idaho		10.2%
4. Montana		9.3%
5. North Dakota		9.0%

Bottom 5 "Doc visit: 5+ years ago" states:
1. Rhode Island		3.0%
2. Massachusetts		3.1%
3. Maryland		3.6%
4. Connecticut		3.6%
5. New Jersey		3.7%



Top 5 "Doc visit: Never" states:
1. Texas		1.7%
2. Oklahoma		1.6%
3. Nevada		1.5%
4. New Mexico		1.5%
5. Wyoming		1.4%

Bottom 5 "Doc visit: Never" states:
1. Maine		0.2%
2. Vermont		0.4%
3. Massachusetts		0.5%
4. Connecticut		0.5%
5. Michigan		0.6%


<div class='alert alert-block alert-info'>
   ...<br>...<br>...<br>
   </div>

### 3.3 General health

In [167]:
map_list = ['General health: Excellent',
              'General health: Very good',
              'General health: Good',
              'General health: Fair',
              'General health: Poor']

for m in map_list:
    plot_map(m)

Top 5 "General health: Excellent" states:
1. Massachusetts		22.4%
2. Utah		21.9%
3. Connecticut		21.9%
4. New Jersey		21.3%
5. Colorado		21.1%


Top 5 "General health: Very good" states:
1. Vermont		37.8%
2. New Hampshire		37.4%
3. Minnesota		37.4%
4. Colorado		36.4%
5. Maine		36.2%


Top 5 "General health: Good" states:
1. Hawaii		34.8%
2. Texas		34.2%
3. Mississippi		33.9%
4. Nevada		33.8%
5. Oklahoma		33.2%


Top 5 "General health: Fair" states:
1. West Virginia		16.9%
2. Arkansas		16.5%
3. Mississippi		15.8%
4. Kentucky		15.6%
5. Alabama		15.5%


Top 5 "General health: Poor" states:
1. West Virginia		8.3%
2. Kentucky		7.3%
3. Mississippi		7.2%
4. Arkansas		7.1%
5. Alabama		6.4%


<div class='alert alert-block alert-info'>
   ...<br>...<br>...<br>
   </div>

### 3.4 Mental health

In [168]:
map_list = ['Concentrate, remember, decide: Difficult',
              'Bad mental health days: 0',
              'Bad mental health days: 1-13',
              'Bad mental health days: 14+']

for m in map_list:
    plot_map(m)

Top 5 "Concentrate, remember, decide: Difficult" states:
1. West Virginia		17.2%
2. Louisiana		16.0%
3. Kentucky		15.9%
4. Mississippi		15.8%
5. Arkansas		15.6%


Top 5 "Bad mental health days: 0" states:
1. Hawaii		66.3%
2. Florida		65.8%
3. South Dakota		65.6%
4. Mississippi		64.9%
5. North Carolina		64.7%


Top 5 "Bad mental health days: 1-13" states:
1. Utah		32.0%
2. Washington		29.3%
3. Vermont		29.3%
4. Colorado		29.2%
5. Wisconsin		28.2%


Top 5 "Bad mental health days: 14+" states:
1. West Virginia		19.2%
2. Arkansas		18.0%
3. Louisiana		18.0%
4. Kentucky		17.5%
5. Alabama		17.2%


<div class='alert alert-block alert-info'>
   ...<br>...<br>...<br>
   </div>

### 3.5 Dietary health

In [169]:
map_list = ['Fruit eaten: Daily',
            'Vegetables eaten: Daily']

for m in map_list:
    plot_map(m)

Top 5 "Fruit eaten: Daily" states:
1. Vermont		67.7%
2. Massachusetts		66.4%
3. New Hampshire		66.3%
4. Connecticut		66.0%
5. Maine		65.8%


Top 5 "Vegetables eaten: Daily" states:
1. Maine		85.9%
2. Vermont		85.8%
3. New Hampshire		84.5%
4. Oregon		83.6%
5. Idaho		83.2%


<div class='alert alert-block alert-info'>
   ...<br>...<br>...<br>
   </div>

### 3.6 Physical activity

In [170]:
map_list = ['Aerobic activity per week: Over 150 min',
            'Met physical activity guidelines: Yes',
            'Strength training: 2x+ per week',
            'Physically active in last month: Yes']

for m in map_list:
    plot_map(m)

Top 5 "Aerobic activity per week: Over 150 min" states:
1. Vermont		60.0%
2. Colorado		59.2%
3. Montana		58.4%
4. Washington		58.3%
5. Oregon		57.9%


Top 5 "Met physical activity guidelines: Yes" states:
1. Colorado		26.5%
2. Montana		24.7%
3. Alaska		24.7%
4. Vermont		24.6%
5. Hawaii		24.3%


Top 5 "Strength training: 2x+ per week" states:
1. Colorado		36.7%
2. Hawaii		35.5%
3. Utah		35.5%
4. Alaska		35.5%
5. New Mexico		34.9%


Top 5 "Physically active in last month: Yes" states:
1. Colorado		82.6%
2. Utah		82.0%
3. Washington		81.7%
4. Vermont		80.3%
5. Oregon		80.1%


<div class='alert alert-block alert-info'>
   ...<br>...<br>...<br>
   </div>

# 4. Conclusion

<div class='alert alert-block alert-warning'>
    <b>Summary</b><br><br>
    <li><b>....</b><br>
    <li><b>...</b><br>
    <br>
    <li>...<br>
    <li>...<br>
    <li>...<br>
   </div>

<div class='alert alert-block alert-success'>
    <b>Next steps</b><br><br>
    <li>...<br>
    <li>...<br>
    <li>...
   </div>

In [ ]:
# reset plot defaults

sns.reset_defaults()